In [1]:
!pip install transformers 
!pip install datasets
!pip install langchain
!pip install boto3
!pip install datarobotx

  Obtaining dependency information for boto3 from https://files.pythonhosted.org/packages/e2/ff/0461ebdf386a7adfa24886ea53c5f8f769bee6f1d054473afd5390b9868b/boto3-1.28.75-py3-none-any.whl.metadata
  Obtaining dependency information for botocore<1.32.0,>=1.31.75 from https://files.pythonhosted.org/packages/c5/d1/614208083494f51454f667ecc52da479b6c3445f23071ee14c3fe9f4b5ac/botocore-1.31.75-py3-none-any.whl.metadata
  Obtaining dependency information for s3transfer<0.8.0,>=0.7.0 from https://files.pythonhosted.org/packages/5a/4b/fec9ce18f8874a96c5061422625ba86c3ee1e6587ccd92ff9f5bf7bd91b2/s3transfer-0.7.0-py3-none-any.whl.metadata
   ---------------------------------------- 0.0/135.8 kB ? eta -:--:--
   ---------------------------------------- 135.8/135.8 kB 4.1 MB/s eta 0:00:00
   ---------------------------------------- 0.0/11.3 MB ? eta -:--:--
   --- ------------------------------------ 1.0/11.3 MB 30.4 MB/s eta 0:00:01
   ----- ---------------------------------- 1.6/11.3 MB 20.2 MB/s

  Obtaining dependency information for datarobotx from https://files.pythonhosted.org/packages/8d/5d/9b2297c85795719143445cb32eba85f5d6e501fa917edd431ebf91750c9f/datarobotx-0.1.19-py3-none-any.whl.metadata
  Using cached altair-4.2.2-py3-none-any.whl (813 kB)
  Obtaining dependency information for datarobot>=3.2.0 from https://files.pythonhosted.org/packages/a0/2a/f9f07bdfb7de7735c591ecc9cd800f8977117f2b41aa5dde13b35083c37b/datarobot-3.2.1-py3-none-any.whl.metadata
     ---------------------------------------- 0.0/54.5 kB ? eta -:--:--
     ---------------------------------------- 54.5/54.5 kB 2.9 MB/s eta 0:00:00
  Obtaining dependency information for strenum>=0.4.15 from https://files.pythonhosted.org/packages/81/69/297302c5f5f59c862faa31e6cb9a4cd74721cd1e052b38e464c5b402df8b/StrEnum-0.4.15-py3-none-any.whl.metadata
  Obtaining dependency information for cmdkit>=2.1.2 from https://files.pythonhosted.org/packages/53/ed/8c77f446c5524e67fe8e28064b4c1bd0b7757cdbbfab95e0aa41baac595b/cmdki

# Imports and Initialization

In [2]:
import boto3
from langchain.llms.bedrock import Bedrock
from langchain.chains import LLMChain
import requests
from typing import Dict, Any
from langchain.prompts import PromptTemplate
from datarobotx.llm import enrich
import json
import re

In [4]:
import os

AWS_ACCESS_KEY_ID = os.environ['AWS_ACCESS_KEY_ID']
AWS_SECRET_ACCESS_KEY = os.environ['AWS_SECRET_ACCESS_KEY']
HF_API_TOKEN = os.environ['HF_API_TOKEN']

In [3]:
BEDROCK_CLIENT = boto3.client("bedrock-runtime",
                              'us-east-1')
llm = Bedrock(model_id="anthropic.claude-v2",
              client=BEDROCK_CLIENT)
llm.model_kwargs = {'temperature': 0.0, "max_tokens_to_sample": 2048}

# Fetch and Prepare Data

In [5]:
from datasets import load_dataset

# Load IMDb dataset
dataset = load_dataset('rungalileo/medical_transcription_40')

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/4499 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/500 [00:00<?, ? examples/s]

In [6]:
dataset['train']

Dataset({
    features: ['id', 'text', 'label'],
    num_rows: 4499
})

In [7]:
import pandas as pd

df = dataset['train'].to_pandas()
import pandas as pd

# Assume df is your DataFrame
filtered_df = df[df['label'] == 36]


In [8]:
filtered_df = filtered_df[0:1]

# Use AWS Medical Comprehend to do Entity Recognition

In [9]:
import boto3

def analyze_medical_text(text, region='us-east-1'):
    """
    Analyze medical text using Amazon Comprehend Medical.

    :param text: The text string to be analyzed
    :param region: The AWS region where Amazon Comprehend Medical is available
    """
    # Create a Boto3 client
    client = boto3.client(service_name='comprehendmedical', region_name=region)

    # Analyze medical entities
    try:
        result = client.detect_entities_v2(Text=text)
        return result

    except Exception as e:
        print("Error:", str(e))


## Expand the Entity elements into statements for the LLM

In [10]:
def expand_entity(json_dict):
    try:
        # Parsing the main entity
        entity_id = json_dict.get("Id")
        entity_text = json_dict.get("Text")
        entity_category = json_dict.get("Category")
        entity_type = json_dict.get("Type")
        entity_score = json_dict.get("Score")
        entity_begin_offset = json_dict.get("BeginOffset")
        entity_end_offset = json_dict.get("EndOffset")

        # Constructing the main entity statement
        statement = f"Entity ID {entity_id} represents a text segment '{entity_text}' categorized as {entity_category} " \
                    f"with the type {entity_type}. The segment starts at offset {entity_begin_offset} and ends at " \
                    f"offset {entity_end_offset}, having a confidence score of {entity_score:.4f}."

        # Parsing attributes, if any
        attributes = json_dict.get("Attributes", [])
        for attr in attributes:
            attr_type = attr.get("Type")
            attr_score = attr.get("Score")
            attr_relationship_score = attr.get("RelationshipScore")
            attr_relationship_type = attr.get("RelationshipType")
            attr_id = attr.get("Id")
            attr_begin_offset = attr.get("BeginOffset")
            attr_end_offset = attr.get("EndOffset")
            attr_text = attr.get("Text")
            attr_category = attr.get("Category")

            # Constructing the attribute statement
            attr_statement = f"\n\nAttribute ID {attr_id} is associated with Entity ID {entity_id}. It represents a " \
                             f"text segment '{attr_text}' categorized as {attr_category} with the type {attr_type}. " \
                             f"The segment starts at offset {attr_begin_offset} and ends at offset {attr_end_offset}, " \
                             f"having a confidence score of {attr_score:.4f}. The relationship between the main " \
                             f"entity and this attribute is of type {attr_relationship_type} and has a confidence " \
                             f"score of {attr_relationship_score:.4f}."

            statement += attr_statement

        return statement

    except Exception as e:
        return f"An error occurred: {str(e)}"

In [11]:
import json

def expand_entities(entity_resolution):
    entities = []
    for entity in entity_resolution['Entities']:
        entities.append(expand_entity(entity))
    return "\n-------------\n".join(entities)

In [12]:
filtered_df['entity_resolution_bronze'] = filtered_df.apply(lambda row: analyze_medical_text(row['text']), 
                                                            axis=1)
filtered_df['entity_resolution_silver'] = filtered_df.apply(lambda row: expand_entities(row['entity_resolution_bronze']),
                                                            axis=1)

filtered_df.head()

id                                               text  label  \
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   

                            entity_resolution_bronze  \
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   

                            entity_resolution_silver  
4  Entity ID 76 represents a text segment 'Lump' ...

# Extract the Diagnoses from the Medical Note

In [13]:
def extract_diagnoses(llm, text: str, er: str) -> Dict:
    """
    Extracts clinical attributes from a rationale.
    
    Parameters:
    rationale (str): The rationale to be processed.
    
    Returns:
    List[str]: A list of clinical attributes.
    """
    template = '''Extract each diagnosis as documented in the medical note, formatted as a JSON object with the following attributes: 
- Diagnosis, 
- Supporting Text from the Medical Note

Return the JSON object formatted as the following example:
```json
{{
  "Diagnoses": [{{"Diagnosis": "", "Supporting Text from the Medical Note": ["Supporting text....", "Supporting text....", "Supporting text...."]}},
                          {{"Diagnosis": "", "Supporting Text from the Medical Note": ["Supporting text....", "Supporting text....", "Supporting text...."]}}]
}}
```

Medical Note:
{text}

Entity Resolutions for Medical Note:
{er}

Assistant:
'''
    prompt = PromptTemplate(
        input_variables=["text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(text=text, er=er)
    return output

In [14]:
# df['C'] = df.apply(lambda row: row['A'] + row['B'], axis=1)
filtered_df['diagnoses_bronze'] = filtered_df.apply(lambda row: extract_diagnoses(llm, 
                                                                          row['text'],
                                                                          row['entity_resolution_silver']),
                                       axis=1)

In [15]:
filtered_df.apply(lambda row: print(row['diagnoses_bronze']),
                  axis=1)

 Here is the JSON output containing the extracted diagnoses and supporting text segments from the medical note:
```json
{
  "Diagnoses": [
    {
      "Diagnosis": "Lump in the chest wall",
      "Supporting Text from the Medical Note": [
        "This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient. It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."
      ]
    },
    {
      "Diagnosis": "Hypertension", 
      "Supporting Text from the Medical Note": [
        "Hypertension."
      ]
    },
    {
      "Diagnosis": "Hyperlipidemia",
      "Supporting Text from the Medical Note": [
        "Hyperlipidemia."
      ]
    },
    {
      "Diagnosis": "Glucose intolerance",
      "Supporting Text from the Medical Note": [
        "Glucose intolerance."
      ]
    },
    {
      "Diagnosis": "Chronic obstructive pulmon

In [16]:
import json
import re
from typing import Dict, Any

def extract_and_convert_to_json(text: str) -> Dict[str, Any]:
    """
    Extracts a JSON object from a string of text between markers ```json and ```.
    
    Parameters:
    text (str): The input text containing the JSON object between ```json and ``` markers.
    
    Returns:
    Dict[str, Any]: The extracted JSON object as a dictionary.
    
    Raises:
    ValueError: If no JSON object is found within the specified markers.
    """
    print(text)
    # Define the regex pattern to extract text between ```json and ```
    pattern = re.compile(r'```json\n(.*?)```', re.DOTALL)

    # Search for the pattern in the input text
    match = pattern.search(text)

    # If a match is found, convert the matched text to JSON and return it
    if match:
        json_text = match.group(1)
        json_object = json.loads(json_text)
        return json_object
    else:
        raise ValueError("No JSON found")


In [17]:
filtered_df['diagnoses_silver'] = filtered_df.apply(lambda row: extract_and_convert_to_json(row['diagnoses_bronze'])['Diagnoses'],
                                       axis=1)

 Here is the JSON output containing the extracted diagnoses and supporting text segments from the medical note:
```json
{
  "Diagnoses": [
    {
      "Diagnosis": "Lump in the chest wall",
      "Supporting Text from the Medical Note": [
        "This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient. It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."
      ]
    },
    {
      "Diagnosis": "Hypertension", 
      "Supporting Text from the Medical Note": [
        "Hypertension."
      ]
    },
    {
      "Diagnosis": "Hyperlipidemia",
      "Supporting Text from the Medical Note": [
        "Hyperlipidemia."
      ]
    },
    {
      "Diagnosis": "Glucose intolerance",
      "Supporting Text from the Medical Note": [
        "Glucose intolerance."
      ]
    },
    {
      "Diagnosis": "Chronic obstructive pulmon

In [18]:
filtered_df.apply(lambda row: print(row['diagnoses_silver']),
              axis=1)

[{'Diagnosis': 'Lump in the chest wall', 'Supporting Text from the Medical Note': ['This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient. It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts.']}, {'Diagnosis': 'Hypertension', 'Supporting Text from the Medical Note': ['Hypertension.']}, {'Diagnosis': 'Hyperlipidemia', 'Supporting Text from the Medical Note': ['Hyperlipidemia.']}, {'Diagnosis': 'Glucose intolerance', 'Supporting Text from the Medical Note': ['Glucose intolerance.']}, {'Diagnosis': 'Chronic obstructive pulmonary disease', 'Supporting Text from the Medical Note': ['Chronic obstructive pulmonary disease?']}, {'Diagnosis': 'Tobacco abuse', 'Supporting Text from the Medical Note': ['Tobacco abuse.']}, {'Diagnosis': 'Anal fistula', 'Supporting Text from the Medical Note': ['History of anal fistula.']}, {'Diagn

# Explode the diagnoses into a diagnosis per row

In [19]:
filtered_df = filtered_df.explode('diagnoses_silver')

# Extract the MEAT Criteria

## Monitoring

In [20]:
import time

def extract_disease_monitoring(llm, diagnosis: str, text: str, er: str) -> str:
    print(diagnosis)
    template = '''
    You are an excellent CMS Risk Adjuster auditing a Medical Note. You never document anything not supported by evidence in the Medical Note.
    
    For the diagnosis of {diagnosis}, document the signs, symptoms, disease progression/regression, 
    and ongoing monitoring of the condition (ordering of tests and referencing labs/other tests), 
    formatted as a JSON object with the following attributes:
    - Diagnosis
    - Signs
    - Symptoms
    - Disease Progression
    - Disease Regression
    - Ongoing Monitoring

    Those attributes are defined as:
    - Signs: The Risk Adjuster would assess how the healthcare provider is monitoring and documenting objective indicators of the patient’s health status. This could include vital signs, physical examination findings, or other observable aspects of the patient’s health. They would expect to see regular and consistent documentation that reflects the patient's ongoing condition.
    - Symptoms: The auditor would review the medical note to ensure that subjective indicators of the patient’s condition, as reported by the patient, are being regularly monitored and documented. This includes any changes in symptoms, their severity, and the impact on the patient’s quality of life.
    - Disease Progression: The Risk Adjuster would look for clear documentation showing ongoing monitoring of any progression of the disease. This involves evaluating how the provider is tracking changes in the patient’s condition over time and ensuring that this information is used to adjust the care plan as necessary.
    - Disease Regression: The auditor would assess whether any improvements or regressions in the patient's condition are being closely monitored and documented. They would expect to see evidence that the healthcare provider is tracking any positive changes and adjusting the treatment plan accordingly.
    - Ongoing Monitoring: The Risk Adjuster would evaluate the overall consistency and thoroughness of the ongoing monitoring documented in the medical note. They would expect to see regular updates on the patient's condition, including any changes in signs, symptoms, and the disease's progression or regression.

    Further Guidance:
    - Entity Resolutions for the Medical Note are provided to improve quality but only focus on the diagnosis of {diagnosis}. 
    - Do not include anything in the JSON object not directly referred to in the Medical Note.
    - Ensure the JSON object is encapsulated by an opening ```json and by a ```

    Return the JSON object formatted as the following example:
    ```json
    {{
      "Diagnosis": "",
      "Signs": ["", "”],
      "Symptoms": ["", "”],
      "Disease Progression": ["", "”],
      "Disease Regression": ["", "”],
      "Ongoing Monitoring": ["", "”]
    }}
    ```

    Medical Note:
    {text}

    Entity Resolutions for Medical Note:
    {er}

    Assistant:
    '''
    prompt = PromptTemplate(
        input_variables=["diagnosis", "text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(diagnosis=diagnosis, text=text, er=er)
    print(output)
    time.sleep(5)
    return output


In [21]:
filtered_df['monitoring_bronze'] = filtered_df.apply(lambda row: extract_disease_monitoring(llm, 
                                                                                              row['diagnoses_silver']['Diagnosis'],
                                                                                              row['text'],
                                                                                              row['entity_resolution_silver']
                                                                                   ), 
                                             axis=1)

filtered_df['monitoring_silver'] = filtered_df.apply(lambda row: extract_and_convert_to_json(row['monitoring_bronze']),
                                       axis=1)

filtered_df.head()

Lump in the chest wall


 Here is the formatted JSON object for the diagnosis of Lump in the chest wall based on the given medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Signs": ["2-cm diameter hard mass in relationship to the costosternal cartilages in the lower most position in the left side, just adjacent to the sternum"],
  "Symptoms": ["tender on palpation", "hurts", "when he takes a deep breath also, it hurts"],
  "Disease Progression": ["getting larger"], 
  "Disease Regression": [],
  "Ongoing Monitoring": ["complaining of having had a lump in the chest for the past year or so"]
}
```


Hypertension


 Here is the formatted JSON object for the diagnosis of Hypertension based on the given medical note:
```json
{
  "Diagnosis": "Hypertension",
  "Signs": ["Blood pressure 140/84"],
  "Symptoms": [],
  "Disease Progression": [],
  "Disease Regression": [],
  "Ongoing Monitoring": ["Blood pressure 140/84"] 
}
```


 Here is the formatted JSON object for the diagnosis of Hyperlipidemia based on the given medical note:
```json
{
  "Diagnosis": "Hyperlipidemia",
  "Signs": [],
  "Symptoms": [],
  "Disease Progression": [],
  "Disease Regression": [],
  "Ongoing Monitoring": ["Hyperlipidemia"]
}
```
The medical note does not contain any direct references to signs, symptoms, disease progression, or disease regression related to hyperlipidemia. The only relevant entity is the diagnosis of hyperlipidemia itself under past medical history, which I have included under "Ongoing Monitoring".


...

 Here is the formatted JSON object for the diagnosis of Diabetes based on the given medical note:
```json
{
  "Diagnosis": "Diabetes",
  "Signs": ["Glucose intolerance"],  
  "Symptoms": [],
  "Disease Progression": [],
  "Disease Regression": [],
  "Ongoing Monitoring": [] 
}
```
The medical note mentions "Glucose intolerance" as a chronic/inactive condition, which can be considered a sign of diabetes. No other clear symptoms, disease progression/regression, or ongoing monitoring related to diabetes are documented in the note.


Cancer


 Here is the formatted JSON object for the medical note:
```json
{
  "Diagnosis": "Cancer",
  "Signs": ["Lump in chest wall", "Tender lump in chest"],
  "Symptoms": ["Pain with deep breaths"],  
  "Disease Progression": ["Lump has been getting larger over past year"],
  "Disease Regression": [],
  "Ongoing Monitoring": [] 
}
```
The JSON object contains the requested attributes for the diagnosis of cancer based on the evidence in the medical note. The signs reflect the objective findings of a lump in the chest wall that is tender. The symptom of pain with deep breaths is documented. Disease progression shows the lump has been getting larger over the past year. There is no evidence of disease regression or ongoing monitoring in the note, so those attributes are left blank.


 Here is the formatted JSON object for the diagnosis of Lump in the chest wall based on the given medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Signs": ["2-cm diameter hard mass in relationship to the costosternal cartilages in the lower most position in the left side, just adjacent to the sternum"],
  "Symptoms": ["tender on palpation", "hurts", "when he takes a deep breath also, it hurts"],
  "Disease Progression": ["getting larger"], 
  "Disease Regression": [],
  "Ongoing Monitoring": ["complaining of having had a lump in the chest for the past year or so"]
}
```
 Here is the formatted JSON object for the diagnosis of Hypertension based on the given medical note:
```json
{
  "Diagnosis": "Hypertension",
  "Signs": ["Blood pressure 140/84"],
  "Symptoms": [],
  "Disease Progression": [],
  "Disease Regression": [],
  "Ongoing Monitoring": ["Blood pressure 140/84"] 
}
```
 Here is the formatted JSON object for the diagnosis of Hyperlipidemia based on the given m

id                                               text  label  \
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   

                            entity_resolution_bronze  \
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   

                            entity_resolution_silver  \
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   

                                    diagnoses_bronze  \
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   

                                    diagnoses_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Suppo...   
4  {'Diagnosis': 'Hypertension', 'Supporting Text...   
4  {'Diagnosis': 'Hyperlipidemia', 'Supporting Te...   
4  {'Diagnosis': 'Glucose intolerance', 'Supporti...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   monitoring_bronze  \
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   

                                   monitoring_silver  
4  {'Diagnosis': 'Lump in the chest wall', 'Signs...  
4  {'Diagnosis': 'Hypertension', 'Signs': ['Blood...  
4  {'Diagnosis': 'Hyperlipidemia', 'Signs': [], '...  
4  {'Diagnosis': 'Glucose intolerance', 'Signs': ...  
4  {'Diagnosis': 'Chronic obstructive pulmonary d...

## Evaluation

In [22]:
def extract_disease_evaulation(llm, diagnosis: str, text: str, er: str) -> str:
    print(diagnosis)
    template = '''
    You are an excellent CMS Risk Adjuster auditing a Medical Note. You never document anything not supported by evidence in the Medical Note.
    
    For the diagnosis of {diagnosis}, document the present state of the condition, physical exam findings, 
    test results, medication effectiveness, and response to treatment, formatted as a JSON object with the 
    following attributes: 
    - Diagnosis
    - Present State
    - Physical Exam Findings
    - Test Results
    - Medication Effectiveness
    - Response to Treatment

    Those attributes are defined as:
    - Present State: The Risk Adjuster would check that the current state of the diagnosis is clearly documented and that it is consistent with the rest of the medical note. They want to ensure that any changes, improvements, or worsening of the condition are accurately reflected and supported by clinical evidence.
    - Physical Exam Findings: The auditor would review the documented physical exam findings to ensure they are specific and detailed, directly supporting the diagnosis.
    - Test Results: The Risk Adjuster would check that all relevant test results are documented and that their interpretation supports the diagnosis. They also look to see that any abnormal results are addressed.
    - Medication Effectiveness: The auditor would evaluate the documentation to ensure it reflects the patient’s response to any medications, indicating whether the medications are effective or if adjustments are needed.
    - Response to Treatment: The Risk Adjuster would assess the documentation of the patient’s response to any treatments provided, ensuring it is specific and supported by clinical evidence.

    Further Guidance:
    - Entity Resolutions for the Medical Note are provided to improve quality but only focus on the diagnosis of {diagnosis}. 
    - Do not include anything in the JSON object not directly referred to in the Medical Note.
    - Ensure the JSON object is encapsulated by an opening ```json and by a ```
    
    Return the JSON object formatted as the following example:
    ```json
    {{
      "Diagnosis": "",
      "Present State": ["", ""],
      "Physical Exam Findings": ["", ""],
      "Test Results": ["", ""],
      "Medication Effectiveness": ["", ""],
      "Response to Treatment": ["", ""]
    }}
    ```
    
    Medical Note:
    {text}

    Entity Resolutions for Medical Note:
    {er}
    
    Assistant:
    '''
    prompt = PromptTemplate(
        input_variables=["diagnosis", "text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(diagnosis=diagnosis, text=text, er=er)
    print(output)
    time.sleep(5)
    return output


In [23]:
filtered_df['evaluation_bronze'] = filtered_df.apply(lambda row: extract_disease_evaulation(llm, 
                                                                                            row['diagnoses_silver']['Diagnosis'],
                                                                                            row['text'],row['entity_resolution_silver']
                                                                                   ), 
                                             axis=1)

filtered_df['evaluation_silver'] = filtered_df.apply(lambda row: extract_and_convert_to_json(row['evaluation_bronze']),
                                       axis=1)

filtered_df.head()

Lump in the chest wall


 Here is the JSON object for the diagnosis of Lump in the chest wall based on the provided medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Present State": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.  It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."],
  "Physical Exam Findings": ["There is a localized 2-cm diameter hard mass in relationship to the costosternal cartilages in the lower most position in the left side, just adjacent to the sternum."],
  "Test Results": [], 
  "Medication Effectiveness": [],
  "Response to Treatment": []
}
```


Hypertension


 Here is the formatted JSON object for the diagnosis of Hypertension based on the provided medical note and entity resolutions:
```json
{
  "Diagnosis": "Hypertension",
  "Present State": ["blood pressure 140/84", "on antihypertensive medications"],
  "Physical Exam Findings": ["blood pressure 140/84"],  
  "Test Results": [],
  "Medication Effectiveness": ["on antihypertensive medications"],
  "Response to Treatment": []
}
```


Hyperlipidemia


...

 Here is the JSON object for the diagnosis of Diabetes based on the given medical note:
```json
{
  "Diagnosis": "Diabetes",
  "Present State": ["Glucose intolerance"],
  "Physical Exam Findings": [],  
  "Test Results": [],
  "Medication Effectiveness": [],
  "Response to Treatment": []
}
```


Cancer


 Here is the JSON object for the cancer diagnosis in the medical note, based on the evidence provided:
```json
{
  "Diagnosis": "Lump",
  "Present State": ["past year", "getting larger and tender"],
  "Physical Exam Findings": ["2-cm diameter hard mass", "left side of chest wall"],
  "Test Results": [],
  "Medication Effectiveness": [],
  "Response to Treatment": []  
}
```


 Here is the JSON object for the diagnosis of Lump in the chest wall based on the provided medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Present State": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.  It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."],
  "Physical Exam Findings": ["There is a localized 2-cm diameter hard mass in relationship to the costosternal cartilages in the lower most position in the left side, just adjacent to the sternum."],
  "Test Results": [], 
  "Medication Effectiveness": [],
  "Response to Treatment": []
}
```
 Here is the formatted JSON object for the diagnosis of Hypertension based on the provided medical note and entity resolutions:
```json
{
  "Diagnosis": "Hypertension",
  "Present State": ["blood pressure 140/84", "on antihypertensive medications"]

id                                               text  label  \
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   

                            entity_resolution_bronze  \
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   

                            entity_resolution_silver  \
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   

                                    diagnoses_bronze  \
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   

                                    diagnoses_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Suppo...   
4  {'Diagnosis': 'Hypertension', 'Supporting Text...   
4  {'Diagnosis': 'Hyperlipidemia', 'Supporting Te...   
4  {'Diagnosis': 'Glucose intolerance', 'Supporti...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   monitoring_bronze  \
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   

                                   monitoring_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Signs...   
4  {'Diagnosis': 'Hypertension', 'Signs': ['Blood...   
4  {'Diagnosis': 'Hyperlipidemia', 'Signs': [], '...   
4  {'Diagnosis': 'Glucose intolerance', 'Signs': ...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   evaluation_bronze  \
4   Here is the JSON object for the diagnosis of ...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the JSON object for the diagnosis of ...   
4   Here is the JSON object for the diagnosis of ...   

                                   evaluation_silver  
4  {'Diagnosis': 'Lump in the chest wall', 'Prese...  
4  {'Diagnosis': 'Hypertension', 'Present State':...  
4  {'Diagnosis': 'Hyperlipidemia', 'Present State...  
4  {'Diagnosis': 'Glucose intolerance', 'Present ...  
4  {'Diagnosis': 'Chronic obstructive pulmonary d...

## Assess and Address

In [24]:
def extract_disease_address_and_assess(llm, diagnosis: str, text: str, er: str) -> str:
    print(diagnosis)
    template = '''
    You are an excellent CMS Risk Adjuster auditing a Medical Note. You never document anything not supported by evidence in the Medical Note.
    
    For the diagnosis of {diagnosis}, document the discussion of the chronic condition, review of records, 
    counseling, acknowledgment, documentation status/level of condition, how the chronic condition will be 
    evaluated, and ordering of further tests, formatted as a JSON object with the following attributes:
    - Diagnosis
    - Discussion
    - Review of Records
    - Counseling
    - Acknowledgment
    - Status/Level of Condition
    - Evaluation Plans
    - Further Tests Ordered

    The definition of these attributes are as follows:
    - Diagnosis: The Risk Adjuster will check if the diagnosis is clearly stated and supported by the clinical evidence documented in the medical note. They will look for specificity and ensure that the diagnosis aligns with ICD-10 coding guidelines.
    - Discussion: The auditor will evaluate if there is detailed documentation of discussions between the provider and the patient, or among different healthcare providers, regarding the patient’s condition. This could also include discussions about differential diagnoses and the provider’s thought process.
    - Review of Records: The Risk Adjuster will look for evidence that the provider has reviewed and incorporated previous medical records and history into the patient’s current evaluation. This shows that the provider is taking into account all available information to make an accurate diagnosis.
    - Counseling: The auditor will assess if the medical note includes documentation of counseling provided to the patient about their condition, treatment options, and potential outcomes. This reflects that the provider is engaging the patient in their care and ensuring they are informed.
    - Acknowledgment: The Risk Adjuster will check that the provider has acknowledged and documented the patient’s reported symptoms and concerns, demonstrating that these factors were considered in the evaluation and treatment planning.
    - Status/Level of Condition: The auditor will review the documentation to ensure that the current status or severity of the patient’s condition is clearly stated and supported by clinical evidence. This is crucial for accurate risk adjustment.
    - Evaluation Plans: The Risk Adjuster will evaluate if there are clear plans documented for further evaluation or monitoring of the patient’s condition. This could include plans for follow-up visits, additional tests, or consultations with specialists.
    - Further Tests Ordered: The auditor will look for documentation of any additional tests that have been ordered to further assess the patient’s condition. They will check that these tests are justified based on the patient’s symptoms and condition, and that the results are incorporated into the patient’s care plan.

    Further Guidance:
    - Entity Resolutions for the Medical Note are provided to improve quality but only focus on the diagnosis of {diagnosis}. 
    - Do not include anything in the JSON object not directly referred to in the Medical Note.
    - Ensure the JSON object is encapsulated by an opening ```json and by a ```
    
    Return the JSON object formatted as the following example:
    ```json
    {{
      "Diagnosis": "",
      "Discussion": ["", ""],
      "Review of Records": ["", ""],
      "Counseling": ["", ""],
      "Acknowledgment": ["", ""],
      "Status/Level of Condition": ["", ""],
      "Evaluation Plans": ["", ""],
      "Further Tests Ordered": ["", ""]
    }}
    ```
    
    Medical Note:
    {text}

    Entity Resolutions for the Medical Note:
    {er}
    
    Assistant:
    '''
    prompt = PromptTemplate(
        input_variables=["diagnosis", "text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(diagnosis=diagnosis, text=text, er=er)
    print(output)
    time.sleep(5)
    print('-------------')
    return output


In [25]:
filtered_df['assess_bronze'] = filtered_df.apply(lambda row: extract_disease_address_and_assess(llm, 
                                                                                                  row['diagnoses_silver']['Diagnosis'],
                                                                                                  row['text'],
                                                                                                  row['entity_resolution_silver']
                                                                                   ), 
                                             axis=1)

filtered_df['assess_silver'] = filtered_df.apply(lambda row: extract_and_convert_to_json(row['assess_bronze']),
                                       axis=1)

filtered_df.head()

Lump in the chest wall


 Here is the JSON object for the diagnosis of Lump in the chest wall based on the given medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Discussion": ["Patient reports having a lump in the chest wall for about a year", "Patient states the lump has been getting larger and more tender"],
  "Review of Records": [],
  "Counseling": [],
  "Acknowledgment": ["On exam there is a palpable, tender 2 cm mass related to the left lower chest wall"],
  "Status/Level of Condition": ["Lump has been present for about a year", "Lump is getting larger and more tender"],
  "Evaluation Plans": [],
  "Further Tests Ordered": [] 
}
```


-------------
Hypertension


 ```json
{
  "Diagnosis": "Hypertension",
  "Discussion": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.", "He has hypertension that has been discussed."],
  "Review of Records": ["His medical history includes hypertension, hyperlipidemia, glucose intolerance, and tobacco abuse."],
  "Counseling": ["The provider should document any counseling provided to the patient regarding hypertension."],
  "Acknowledgment": ["The provider acknowledges the patient's reported symptoms related to hypertension."],
  "Status/Level of Condition": ["Hypertension is listed as a chronic, inactive condition."],
  "Evaluation Plans": ["The provider should document plans for continued monitoring and evaluation of the patient's hypertension."],
  "Further Tests Ordered": ["No further tests specifically for hypertension are documented as being ordered."]
}
```


-------------
Hyperlipidemia


...

 ```json
{
  "Diagnosis": "Diabetes",
  "Discussion": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.", "It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."],
  "Review of Records": ["Hypertension.", "Hyperlipidemia.", "Glucose intolerance.", "Chronic obstructive pulmonary disease?", "Tobacco abuse.", "History of anal fistula."],
  "Counseling": [],
  "Acknowledgment": [],
  "Status/Level of Condition": [],
  "Evaluation Plans": [],
  "Further Tests Ordered": []
}
```


-------------
Cancer


 ```json
{
  "Diagnosis": "Cancer",
  "Discussion": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.", "It is tender on palpation and also he feels like, when he takes a deep breath also, it hurts."],
  "Review of Records": ["Hypertension.", "Hyperlipidemia.", "Glucose intolerance.", "Chronic obstructive pulmonary disease?", "Tobacco abuse.", "History of anal fistula.", "See above."],
  "Counseling": ["Anal fistulectomy, incision and drainage of perirectal abscess, hand surgery, colonoscopy, arm nerve surgery, and back surgery."],  
  "Acknowledgment": ["He had a broken ankle in the past. They questioned the patient who is a truck driver whether he has had an auto accident in the past, he said that he has not had anything major. He said he bumped his head once, but not his chest, although he told the nurse that a car fell on his chest that is six year

-------------
 Here is the JSON object for the diagnosis of Lump in the chest wall based on the given medical note:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Discussion": ["Patient reports having a lump in the chest wall for about a year", "Patient states the lump has been getting larger and more tender"],
  "Review of Records": [],
  "Counseling": [],
  "Acknowledgment": ["On exam there is a palpable, tender 2 cm mass related to the left lower chest wall"],
  "Status/Level of Condition": ["Lump has been present for about a year", "Lump is getting larger and more tender"],
  "Evaluation Plans": [],
  "Further Tests Ordered": [] 
}
```
 ```json
{
  "Diagnosis": "Hypertension",
  "Discussion": ["This is a 56-year-old white male who has been complaining of having had a lump in the chest for the past year or so and it has been getting larger and tender according to the patient.", "He has hypertension that has been discussed."],
  "Review of Records": ["His medical history inclu

id                                               text  label  \
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   

                            entity_resolution_bronze  \
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   

                            entity_resolution_silver  \
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   

                                    diagnoses_bronze  \
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   

                                    diagnoses_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Suppo...   
4  {'Diagnosis': 'Hypertension', 'Supporting Text...   
4  {'Diagnosis': 'Hyperlipidemia', 'Supporting Te...   
4  {'Diagnosis': 'Glucose intolerance', 'Supporti...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   monitoring_bronze  \
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   

                                   monitoring_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Signs...   
4  {'Diagnosis': 'Hypertension', 'Signs': ['Blood...   
4  {'Diagnosis': 'Hyperlipidemia', 'Signs': [], '...   
4  {'Diagnosis': 'Glucose intolerance', 'Signs': ...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   evaluation_bronze  \
4   Here is the JSON object for the diagnosis of ...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the JSON object for the diagnosis of ...   
4   Here is the JSON object for the diagnosis of ...   

                                   evaluation_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Prese...   
4  {'Diagnosis': 'Hypertension', 'Present State':...   
4  {'Diagnosis': 'Hyperlipidemia', 'Present State...   
4  {'Diagnosis': 'Glucose intolerance', 'Present ...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                       assess_bronze  \
4   Here is the JSON object for the diagnosis of ...   
4   ```json\n{\n  "Diagnosis": "Hypertension",\n ...   
4   ```json\n{\n  "Diagnosis": "Hyperlipidemia",\...   
4   ```json\n{\n  "Diagnosis": "Glucose intoleran...   
4   ```json\n{\n  "Diagnosis": "Chronic obstructi...   

                                       assess_silver  
4  {'Diagnosis': 'Lump in the chest wall', 'Discu...  
4  {'Diagnosis': 'Hypertension', 'Discussion': ['...  
4  {'Diagnosis': 'Hyperlipidemia', 'Discussion': ...  
4  {'Diagnosis': 'Glucose intolerance', 'Discussi...  
4  {'Diagnosis': 'Chronic obstructive pulmonary d...

## Treatment

In [36]:
def extract_disease_treatment(llm, diagnosis: str, text: str, er: str) -> str:
    print(diagnosis)
    template = '''
    You are an excellent CMS Risk Adjuster auditing a Medical Note. You never document anything not supported by evidence in the Medical Note.
    
    For the diagnosis of {diagnosis}, document the care being provided for the condition, prescribing or 
    continuation of medications, referral to specialist, ordering diagnostic tests, therapeutic services, 
    other modalities, and plan for managing the chronic condition, formatted as a JSON object with the 
    following attributes:
    - Diagnosis
    - Care Provided
    - Medications Prescribed
    - Specialist Referral
    - Diagnostic Tests Ordered
    - Therapeutic Services
    - Other Modalities
    - Management Plan

    The attributes are defined as:
    - Care Provided: The Risk Adjuster would assess the documentation to ensure that all care provided to the patient is appropriately recorded. They would check that the provided care is medically necessary and aligned with the patient’s diagnosis and condition.
    - Medications Prescribed: The auditor would review the medical note to ensure that all prescribed medications are documented, along with the dosages and directions for use. They would also check that the prescriptions are appropriate for the patient’s condition and that any potential drug interactions or contraindications are addressed.
    - Specialist Referral: The Risk Adjuster would assess whether referrals to specialists are documented and justified based on the patient’s condition. They would ensure that the purpose of the referral and the expected outcomes are clearly stated.
    - Diagnostic Tests Ordered: The auditor would review the documentation to ensure that any diagnostic tests ordered are relevant to the patient’s symptoms or condition, and that the rationale for ordering these tests is clearly articulated.
    - Therapeutic Services: The Risk Adjuster would evaluate whether any therapeutic services provided are documented and justified. They would check that these services are appropriate for the patient’s condition and that their implementation is based on best practices.
    - Other Modalities: The auditor would assess the use of any other treatment modalities, ensuring that they are appropriately documented and justified based on the patient’s condition.
    - Management Plan: The Risk Adjuster would evaluate the comprehensive management plan documented in the medical note, ensuring that it addresses the patient’s condition in a holistic manner. They would check that the plan includes all necessary components of treatment, follow-up, and ongoing care.

    Further Guidance:
    - Entity Resolutions for the Medical Note are provided to improve quality but only focus on the diagnosis of {diagnosis}. 
    - Do not include anything in the JSON object not directly referred to in the Medical Note.
    - Ensure the JSON object is encapsulated by an opening ```json and by a ```
    
    Return the JSON object formatted as the following example:
    ```json
    {{
      "Diagnosis": "",
      "Care Provided": ["", ""],
      "Medications Prescribed": ["", ""],
      "Specialist Referral": ["", ""],
      "Diagnostic Tests Ordered": ["", ""],
      "Therapeutic Services": ["", ""],
      "Other Modalities": ["", ""],
      "Management Plan": ["", ""]
    }}
    ```
    
    Medical Note:
    {text}

    Entity Resolutions for the Medical Note:
    {er}
    
    Assistant:
    '''
    prompt = PromptTemplate(
        input_variables=["diagnosis", "text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(diagnosis=diagnosis, text=text, er=er)
    print(output)
    print('--------')
    time.sleep(15)
    return output


In [37]:
filtered_df['treatment_bronze'] = filtered_df.apply(lambda row: extract_disease_treatment(llm, 
                                                                                          row['diagnoses_silver']['Diagnosis'],
                                                                                          row['text'],
                                                                                          row['entity_resolution_silver']
                                                                                   ), 
                                             axis=1)

filtered_df['treatment_silver'] = filtered_df.apply(lambda row: extract_and_convert_to_json(row['treatment_bronze']),
                                       axis=1)

filtered_df.head()

Lump in the chest wall


 Here is the formatted JSON object for the diagnosis of Lump in the chest wall based on the provided medical note and entity resolutions:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Care Provided": ["Physical examination"],
  "Medications Prescribed": [],
  "Specialist Referral": [],
  "Diagnostic Tests Ordered": [],
  "Therapeutic Services": [],
  "Other Modalities": [],
  "Management Plan": [] 
}
```
The medical note focuses on documenting the patient's chief complaint of a lump in the chest wall, along with the history and physical exam findings. The entity resolutions identify the lump diagnosis and its location in the chest wall. Since no other care, medications, referrals, tests, services, modalities, or management plans are documented related to this diagnosis, the respective attributes in the JSON object are left blank. Let me know if you would like me to clarify or expand on anything!
--------


Hypertension


 Here is the formatted JSON object for the diagnosis of Hypertension based on the provided medical note and entity resolutions:
```json
{
  "Diagnosis": "Hypertension",
  "Care Provided": ["Prescribing antihypertensive medications"],
  "Medications Prescribed": ["Lisinopril", "Metoprolol", "Felodipine"],
  "Specialist Referral": [],
  "Diagnostic Tests Ordered": [],
  "Therapeutic Services": [],
  "Other Modalities": [],
  "Management Plan": ["Continue prescribed antihypertensive medications", "Follow up with primary care provider"]  
}
```
Key points:
- The diagnosis of Hypertension is directly mentioned in the medical note
- Care provided includes prescribing appropriate antihypertensive medications listed in the note 
- No specialist referrals, diagnostic tests, therapeutic services, or other modalities are mentioned
- Management plan focuses on continuing current medications and follow up
Let me know if you would like me to clarify or expand on any part of the JSON object. I aimed 

Hyperlipidemia


...

 Here is the formatted JSON object for the medical note focusing on the diagnosis of Diabetes:
```json
{
  "Diagnosis": "Diabetes",
  "Care Provided": ["Glucose intolerance"],  
  "Medications Prescribed": ["Metformin 500mg twice daily"],
  "Specialist Referral": ["Endocrinology"],
  "Diagnostic Tests Ordered": ["HbA1c", "Fasting glucose"],
  "Therapeutic Services": ["Diabetes education"],
  "Other Modalities": [],
  "Management Plan": ["Lifestyle modification with diet and exercise", "Medication compliance", "Self glucose monitoring", "Follow up in 3 months"] 
}
```
Key points:
- The diagnosis of Diabetes is directly stated in the medical note 
- Care provided is noted as glucose intolerance, indicating impaired glucose metabolism
- Metformin is a common medication for diabetes, with typical dosing listed
- Referral to endocrinology (diabetes specialists) is appropriate
- Relevant diagnostic tests like HbA1c and fasting glucose are ordered
- Diabetes education is a standard therapeuti

Cancer


 Here is the formatted JSON object for the medical note:
```json
{
  "Diagnosis": "Lump in chest wall",
  "Care Provided": ["Patient reported having lump for about a year", "Lump described as getting larger and tender", "Lump tender on palpation", "Hurts when taking deep breath"],
  "Medications Prescribed": [],
  "Specialist Referral": [],
  "Diagnostic Tests Ordered": [],
  "Therapeutic Services": [],
  "Other Modalities": [],
  "Management Plan": []  
}
```
Key points:
- The diagnosis of "Lump in chest wall" was extracted from the medical note based on the entity resolution.
- Relevant care provided for this diagnosis was extracted, including the patient-reported history and physical exam findings.
- No medications, referrals, diagnostic tests, therapies, other treatments, or management plans related specifically to this diagnosis were documented in the provided medical note.
- The JSON object contains all attributes requested in the desired format.
- Only information directly suppo

 Here is the formatted JSON object for the diagnosis of Lump in the chest wall based on the provided medical note and entity resolutions:
```json
{
  "Diagnosis": "Lump in the chest wall",
  "Care Provided": ["Physical examination"],
  "Medications Prescribed": [],
  "Specialist Referral": [],
  "Diagnostic Tests Ordered": [],
  "Therapeutic Services": [],
  "Other Modalities": [],
  "Management Plan": [] 
}
```
The medical note focuses on documenting the patient's chief complaint of a lump in the chest wall, along with the history and physical exam findings. The entity resolutions identify the lump diagnosis and its location in the chest wall. Since no other care, medications, referrals, tests, services, modalities, or management plans are documented related to this diagnosis, the respective attributes in the JSON object are left blank. Let me know if you would like me to clarify or expand on anything!
 Here is the formatted JSON object for the diagnosis of Hypertension based on the p

id                                               text  label  \
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   
4  3437  CHIEF COMPLAINT:,  Lump in the chest wall.,HIS...     36   

                            entity_resolution_bronze  \
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   
4  {'Entities': [{'Id': 76, 'BeginOffset': 19, 'E...   

                            entity_resolution_silver  \
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   
4  Entity ID 76 represents a text segment 'Lump' ...   

                                    diagnoses_bronze  \
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   
4   Here is the JSON output containing the extrac...   

                                    diagnoses_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Suppo...   
4  {'Diagnosis': 'Hypertension', 'Supporting Text...   
4  {'Diagnosis': 'Hyperlipidemia', 'Supporting Te...   
4  {'Diagnosis': 'Glucose intolerance', 'Supporti...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   monitoring_bronze  \
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   

                                   monitoring_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Signs...   
4  {'Diagnosis': 'Hypertension', 'Signs': ['Blood...   
4  {'Diagnosis': 'Hyperlipidemia', 'Signs': [], '...   
4  {'Diagnosis': 'Glucose intolerance', 'Signs': ...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                   evaluation_bronze  \
4   Here is the JSON object for the diagnosis of ...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the JSON object for the diagnosis of ...   
4   Here is the JSON object for the diagnosis of ...   

                                   evaluation_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Prese...   
4  {'Diagnosis': 'Hypertension', 'Present State':...   
4  {'Diagnosis': 'Hyperlipidemia', 'Present State...   
4  {'Diagnosis': 'Glucose intolerance', 'Present ...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                       assess_bronze  \
4   Here is the JSON object for the diagnosis of ...   
4   ```json\n{\n  "Diagnosis": "Hypertension",\n ...   
4   ```json\n{\n  "Diagnosis": "Hyperlipidemia",\...   
4   ```json\n{\n  "Diagnosis": "Glucose intoleran...   
4   ```json\n{\n  "Diagnosis": "Chronic obstructi...   

                                       assess_silver  \
4  {'Diagnosis': 'Lump in the chest wall', 'Discu...   
4  {'Diagnosis': 'Hypertension', 'Discussion': ['...   
4  {'Diagnosis': 'Hyperlipidemia', 'Discussion': ...   
4  {'Diagnosis': 'Glucose intolerance', 'Discussi...   
4  {'Diagnosis': 'Chronic obstructive pulmonary d...   

                                    treatment_bronze  \
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...   
4   Here is the formatted JSON object for the dia...

In [40]:
pd.set_option('display.max_columns', None)

In [ ]:
def print_selected_columns(row):
    # Define the columns to be printed
    columns_to_print = ["text", 'diagnoses_silver', 'monitoring_silver', 'evaluation_silver', 'assess_silver', 'treatment_silver']

    for c in columns_to_print:
        print(row[c])

    print("****************")

filtered_df.apply(print_selected_columns, axis=1)

MEDICAL_CONDITION
MEDICATION
ANATOMY
TEST_TREATMENT_PROCEDURE
PROTECTED_HEALTH_INFORMATION

In [41]:
import uuid
def generate_random_filename(extension=".txt"):
    random_filename = str(uuid.uuid4()) + extension
    return random_filename

# Markdown Creation

In [42]:
def create_markdown(medical_note, monitoring, evaluation, assess, treatment):
    md_path = f'storage/{generate_random_filename(".md")}'
    if not os.path.exists('storage'):
        os.makedirs('storage')

    # Initialize an empty string to build the Markdown content
    md_content = ""

    # Add medical note
    md_content += "# Medical Note:\n"
    md_content += medical_note + "\n\n"

    # Headers for JSON sections
    json_sections = {
        "Monitoring": monitoring,
        "Evaluation": evaluation,
        "Assess/Address": assess,
        "Treatment": treatment
    }

    # Add JSON sections
    for header, data in json_sections.items():
        md_content += f"# {header}:\n"
        
        # Convert JSON to table and add to Markdown content string
        md_content += "| Attribute | Value |\n"
        md_content += "| --- | --- |\n"
        for key, value in data.items():
            md_content += f"| {key} | {value} |\n"
        md_content += "\n"

    # Write the Markdown content to a file
    with open(md_path, 'w') as md_file:
        md_file.write(md_content)

    print(f"Markdown file created successfully at {md_path}")

    return md_content


In [43]:
filtered_df['markdown'] = filtered_df.apply(lambda row: create_markdown(row['text'],
                                                              row['monitoring_silver'],
                                                              row['evaluation_silver'],
                                                              row['assess_silver'],
                                                              row['treatment_silver']), 
                                             axis=1)

Markdown file created successfully at storage/37747635-bc06-4802-854b-6feccc140677.md
Markdown file created successfully at storage/b8293f0b-7d35-4a15-a407-bcac6e3f81ba.md
Markdown file created successfully at storage/1e6b0abe-30f2-488c-b089-8ca5845a4cb4.md
Markdown file created successfully at storage/e3ea8397-47d4-4699-b28b-25e235076f17.md
Markdown file created successfully at storage/29e0dca8-857e-4ce7-b1da-2d45e6abaa37.md
Markdown file created successfully at storage/be446590-dbc6-464d-9e03-1c34ad710453.md
Markdown file created successfully at storage/71026c06-c87e-46fb-9678-f25350c772c9.md
Markdown file created successfully at storage/d04b4f04-5a4c-4c02-8e9d-f584655502a0.md
Markdown file created successfully at storage/2f7544ed-d0fd-4001-a918-07d707707114.md


In [38]:
!pip install awswrangler

     |████████████████████████████████| 396 kB 12.0 MB/s 


# Write DataFrame to S3 for Downstream systems

In [45]:
import awswrangler as wr

s3_path = f"s3://your-bucket-name/path/to/your/{str(uuid.uuid4())}.parquet"

wr.s3.to_parquet(
    df=filtered_df,
    path=s3_path,
    index=False,
    use_threads=True,
    boto3_session=boto3.Session()  # You can provide custom boto3 session if needed
)

ClientError: An error occurred (AllAccessDisabled) when calling the PutObject operation: All access to this object has been disabled

In [ ]:
def extract_triples(llm, text: str, er: str) -> str:
    template = '''
    Input:
    Medical Note: 
    {text}
    
    Entity Resolution Output:
    {er}

    Task:
    Based on the medical note and the entity resolution output, generate a set of triples in the form of (Subject, Predicate, Object).

    Guidance:
    - Use the Entity Resolution Ouput to define the 'subject' and 'object'.
    - Make the name of the 'subject' and 'object' descriptive as well as include the Entity ID.
    - Use the Medical Note to determine the 'predicate' between the 'subject' and 'object'. Be descriptive with the name of the relationship.
    

    Assistant:
    '''
    prompt = PromptTemplate(
        input_variables=["text", "er"], 
        template=template
    )

    chain = LLMChain(llm=llm, prompt=prompt)
    output = chain.predict(text=text, er=er)
    print(output)
    print('--------')
    time.sleep(5)
    return output

In [ ]:
filtered_df['triples'] = filtered_df.apply(lambda row: extract_triples(llm,
                                                                       row['text'],
                                                                       row['entity_resolution_silver']), 
                                             axis=1)


filtered_df.head()